In [1]:
pip install h3pandas geopandas scikit-learn -q

Note: you may need to restart the kernel to use updated packages.


In [2]:
import geopandas as gpd
import h3pandas
from shapely.geometry import Point, Polygon
from sklearn.preprocessing import MinMaxScaler
import numpy as np
import pandas as pd

In [3]:
schools = gpd.read_file("data/nyc/SchoolPoints_APS_2024_08_28 (1)/SchoolPoints_APS_2024_08_28.shp")
subways = gpd.read_file("data/nyc/nyc_subway_entrances/nyc_subway_entrances.shp")
bike_paths = gpd.read_file("data/nyc/New York City Bike Routes_20241223.geojson")
neighborhoods = gpd.read_file("https://raw.githubusercontent.com/HodgesWardElliott/custom-nyc-neighborhoods/refs/heads/master/custom-pedia-cities-nyc-Mar2018.geojson")
parks = gpd.read_file("data/nyc/Parks Properties_20241223.geojson")

In [4]:
schools = schools.to_crs("EPSG:3857")
subways = subways.to_crs("EPSG:3857")
bike_paths = bike_paths.to_crs("EPSG:3857")
neighborhoods = neighborhoods.to_crs("EPSG:3857")
parks = parks.to_crs("EPSG:3857")

# Analyze neighborhoods

In [5]:
# Analysis for each neighborhood
def analyze_neighborhood(neighborhood_geometry):
    # Count features intersecting the neighborhood boundary
    num_schools = schools[schools.geometry.intersects(neighborhood_geometry)].shape[0]
    num_subways = subways[subways.geometry.intersects(neighborhood_geometry)].shape[0]
    bike_path_length = bike_paths[bike_paths.geometry.intersects(neighborhood_geometry)].length.sum()
    park_area = parks[parks.geometry.intersects(neighborhood_geometry)].area.sum()

    return num_schools, num_subways, bike_path_length, park_area

In [6]:
# Apply analysis to each neighborhood
neighborhoods[['num_schools', 'num_subways', 'bike_path_length', 'park_area']] = neighborhoods.geometry.apply(
    lambda geom: pd.Series(analyze_neighborhood(geom))
)

In [7]:
neighborhoods.head(3)

neighborhood boroughCode        borough  \
0         Allerton           2          Bronx   
1  Alley Pond Park           4         Queens   
2    Arden Heights           5  Staten Island   

                                                X.id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
1  http://nyc.pediacities.com/Resource/Neighborho...   
2  http://nyc.pediacities.com/Resource/Neighborho...   

                                            geometry  num_schools  \
0  POLYGON ((-8220788.214 4993431.406, -8220479.3...         12.0   
1  POLYGON ((-8209070.244 4973902.938, -8209112.6...          0.0   
2  POLYGON ((-8256547.374 4947814.753, -8256546.8...          1.0   

   num_subways  bike_path_length     park_area  
0          5.0      12972.782695  5.191057e+05  
1          0.0       5886.886135  7.365924e+06  
2          0.0          0.000000  9.533262e+06

In [8]:
# Normalize results (0 to 1 scale)
scaler = MinMaxScaler()
columns_to_normalize = ['num_schools', 'num_subways', 'bike_path_length', 'park_area']
neighborhoods[columns_to_normalize] = scaler.fit_transform(neighborhoods[columns_to_normalize])

In [9]:
neighborhoods.head(3)

neighborhood boroughCode        borough  \
0         Allerton           2          Bronx   
1  Alley Pond Park           4         Queens   
2    Arden Heights           5  Staten Island   

                                                X.id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
1  http://nyc.pediacities.com/Resource/Neighborho...   
2  http://nyc.pediacities.com/Resource/Neighborho...   

                                            geometry  num_schools  \
0  POLYGON ((-8220788.214 4993431.406, -8220479.3...     0.193548   
1  POLYGON ((-8209070.244 4973902.938, -8209112.6...     0.000000   
2  POLYGON ((-8256547.374 4947814.753, -8256546.8...     0.016129   

   num_subways  bike_path_length  park_area  
0     0.045045          0.181510   0.026226  
1     0.000000          0.082367   0.372141  
2     0.000000          0.000000   0.481639

In [10]:
# Aggregate results using touching neighborhoods
def aggregate_touching_neighborhoods(neighborhood_index):
    current_geometry = neighborhoods.loc[neighborhood_index, 'geometry']
    touching_indices = neighborhoods[neighborhoods.geometry.touches(current_geometry)].index

    if not touching_indices.empty:
        neighbor_values = neighborhoods.loc[touching_indices, columns_to_normalize].mean()
    else:
        neighbor_values = neighborhoods.loc[neighborhood_index, columns_to_normalize]

    return neighbor_values

In [11]:
# Apply aggregation to each neighborhood
neighborhoods[columns_to_normalize] = neighborhoods.index.to_series().apply(
    lambda idx: aggregate_touching_neighborhoods(idx)
)


In [12]:
# Final normalization (0 to 1 scale)
neighborhoods[columns_to_normalize] = scaler.fit_transform(neighborhoods[columns_to_normalize])

In [13]:
neighborhoods.head(5)

neighborhood boroughCode        borough  \
0         Allerton           2          Bronx   
1  Alley Pond Park           4         Queens   
2    Arden Heights           5  Staten Island   
3        Arlington           5  Staten Island   
4         Arrochar           5  Staten Island   

                                                X.id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
1  http://nyc.pediacities.com/Resource/Neighborho...   
2  http://nyc.pediacities.com/Resource/Neighborho...   
3  http://nyc.pediacities.com/Resource/Neighborho...   
4  http://nyc.pediacities.com/Resource/Neighborho...   

                                            geometry  num_schools  \
0  POLYGON ((-8220788.214 4993431.406, -8220479.3...     0.066667   
1  POLYGON ((-8209070.244 4973902.938, -8209112.6...     0.185185   
2  POLYGON ((-8256547.374 4947814.753, -8256546.8...     0.040741   
3  POLYGON ((-8255425.402 4959593.695, -8255451.0...     0.000000   
4  POLYGON ((-8244408.305 4952520.907, -8244409.6...     0.016667   

   num_subways  bike_path_length  park_area  
0     0.036585          0.009243   0.025121  
1     0.000000          0.203034   0.322221  
2     0.016260          0.079246   0.210843  
3     0.000000          0.000000   0.012868  
4     0.015244          0.080113   0.136984

In [14]:
neighborhoods['index_score'] = neighborhoods['num_schools'] + neighborhoods['num_subways'] + neighborhoods['bike_path_length'] + neighborhoods['park_area'] 

In [15]:
import leafmap

m = leafmap.Map()
m.add_data(
    neighborhoods, column="index_score", scheme="Quantiles", cmap="Blues", legend_title="Index"
)
m

Map(center=[20, 0], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_out_text…

In [16]:
# Save or visualize the results
neighborhoods.to_file("neighborhood_access_index.geojson", driver="GeoJSON")

# Set up the H3 Grid

In [17]:
neighborhoods = neighborhoods.to_crs('EPSG:4326')

In [18]:
resolution = 9  # Adjust resolution as needed
gdf_h3 = neighborhoods.h3.polyfill(resolution)

In [19]:
gdf_h3.head()

neighborhood boroughCode        borough  \
0         Allerton           2          Bronx   
1  Alley Pond Park           4         Queens   
2    Arden Heights           5  Staten Island   
3        Arlington           5  Staten Island   
4         Arrochar           5  Staten Island   

                                                X.id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
1  http://nyc.pediacities.com/Resource/Neighborho...   
2  http://nyc.pediacities.com/Resource/Neighborho...   
3  http://nyc.pediacities.com/Resource/Neighborho...   
4  http://nyc.pediacities.com/Resource/Neighborho...   

                                            geometry  num_schools  \
0  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...     0.066667   
1  POLYGON ((-73.74333 40.73888, -73.74371 40.739...     0.185185   
2  POLYGON ((-74.16983 40.56108, -74.16982 40.561...     0.040741   
3  POLYGON ((-74.15975 40.64142, -74.15998 40.641...     0.000000   
4  POLYGON ((-74.06078 40.59319, -74.06079 40.593...     0.016667   

   num_subways  bike_path_length  park_area  index_score  \
0     0.036585          0.009243   0.025121     0.137616   
1     0.000000          0.203034   0.322221     0.710440   
2     0.016260          0.079246   0.210843     0.347090   
3     0.000000          0.000000   0.012868     0.012868   
4     0.015244          0.080113   0.136984     0.249007   

                                         h3_polyfill  
0  [892a1001067ffff, 892a100102bffff, 892a1001313...  
1  [892a100502bffff, 892a10050d7ffff, 892a100509b...  
2  [892a1060ed7ffff, 892a1060e13ffff, 892a1060163...  
3                                  [892a106267bffff]  
4  [892a107530bffff, 892a107530fffff, 892a1075373...

In [20]:
gdf_h3 = neighborhoods.h3.polyfill(resolution, explode=True)
gdf_h3.head()

neighborhood boroughCode borough  \
0     Allerton           2   Bronx   
0     Allerton           2   Bronx   
0     Allerton           2   Bronx   
0     Allerton           2   Bronx   
0     Allerton           2   Bronx   

                                                X.id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
0  http://nyc.pediacities.com/Resource/Neighborho...   
0  http://nyc.pediacities.com/Resource/Neighborho...   
0  http://nyc.pediacities.com/Resource/Neighborho...   
0  http://nyc.pediacities.com/Resource/Neighborho...   

                                            geometry  num_schools  \
0  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...     0.066667   
0  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...     0.066667   
0  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...     0.066667   
0  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...     0.066667   
0  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...     0.066667   

   num_subways  bike_path_length  park_area  index_score      h3_polyfill  
0     0.036585          0.009243   0.025121     0.137616  892a1001067ffff  
0     0.036585          0.009243   0.025121     0.137616  892a100102bffff  
0     0.036585          0.009243   0.025121     0.137616  892a1001313ffff  
0     0.036585          0.009243   0.025121     0.137616  892a1001397ffff  
0     0.036585          0.009243   0.025121     0.137616  892a1001023ffff

In [21]:
gdf_h3 = gdf_h3[gdf_h3['h3_polyfill'].isnull() == False].set_index('h3_polyfill')
gdf_h3.index.name = None
gdf_h3

neighborhood boroughCode    borough  \
892a1001067ffff     Allerton           2      Bronx   
892a100102bffff     Allerton           2      Bronx   
892a1001313ffff     Allerton           2      Bronx   
892a1001397ffff     Allerton           2      Bronx   
892a1001023ffff     Allerton           2      Bronx   
...                      ...         ...        ...   
892a1008cbbffff       Harlem           1  Manhattan   
892a1008d5bffff       Harlem           1  Manhattan   
892a1008d57ffff       Harlem           1  Manhattan   
892a1008cafffff       Harlem           1  Manhattan   
892a100ab4bffff       Harlem           1  Manhattan   

                                                              X.id  \
892a1001067ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a100102bffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a1001313ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a1001397ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a1001023ffff  http://nyc.pediacities.com/Resource/Neighborho...   
...                                                            ...   
892a1008cbbffff                                               None   
892a1008d5bffff                                               None   
892a1008d57ffff                                               None   
892a1008cafffff                                               None   
892a100ab4bffff                                               None   

                                                          geometry  \
892a1001067ffff  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...   
892a100102bffff  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...   
892a1001313ffff  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...   
892a1001397ffff  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...   
892a1001023ffff  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...   
...                                                            ...   
892a1008cbbffff  POLYGON ((-73.93457 40.82815, -73.93442 40.827...   
892a1008d5bffff  POLYGON ((-73.93457 40.82815, -73.93442 40.827...   
892a1008d57ffff  POLYGON ((-73.93457 40.82815, -73.93442 40.827...   
892a1008cafffff  POLYGON ((-73.93457 40.82815, -73.93442 40.827...   
892a100ab4bffff  POLYGON ((-73.93457 40.82815, -73.93442 40.827...   

                 num_schools  num_subways  bike_path_length  park_area  \
892a1001067ffff     0.066667     0.036585          0.009243   0.025121   
892a100102bffff     0.066667     0.036585          0.009243   0.025121   
892a1001313ffff     0.066667     0.036585          0.009243   0.025121   
892a1001397ffff     0.066667     0.036585          0.009243   0.025121   
892a1001023ffff     0.066667     0.036585          0.009243   0.025121   
...                      ...          ...               ...        ...   
892a1008cbbffff     0.507407     0.278455          0.584689   0.141232   
892a1008d5bffff     0.507407     0.278455          0.584689   0.141232   
892a1008d57ffff     0.507407     0.278455          0.584689   0.141232   
892a1008cafffff     0.507407     0.278455          0.584689   0.141232   
892a100ab4bffff     0.507407     0.278455          0.584689   0.141232   

                 index_score  
892a1001067ffff     0.137616  
892a100102bffff     0.137616  
892a1001313ffff     0.137616  
892a1001397ffff     0.137616  
892a1001023ffff     0.137616  
...                      ...  
892a1008cbbffff     1.511784  
892a1008d5bffff     1.511784  
892a1008d57ffff     1.511784  
892a1008cafffff     1.511784  
892a100ab4bffff     1.511784  

[7465 rows x 10 columns]

In [22]:
gdf_h3 = gdf_h3.h3.h3_to_geo_boundary()

In [23]:
pip install folium matplotlib mapclassify -q

Note: you may need to restart the kernel to use updated packages.


In [24]:
gdf_h3.explore()

In [25]:
gdf_h3_proj = gdf_h3.to_crs('EPSG:3857')

In [26]:
# Analysis for each hex cell
def analyze_access(hex_geometry):
    # Buffer hex geometry
    buffer_1600m = hex_geometry.buffer(1600)
    buffer_800m = hex_geometry.buffer(800)

    # Count features within buffers
    num_schools = schools[schools.geometry.intersects(buffer_1600m)].shape[0]
    num_subways = subways[subways.geometry.intersects(buffer_1600m)].shape[0]
    bike_path_length = bike_paths[bike_paths.geometry.intersects(buffer_1600m)].length.sum()
    park_area = parks[parks.geometry.intersects(buffer_800m)].area.sum()

    return num_schools, num_subways, bike_path_length, park_area

New Dataframe CRS:3857 needed for units in meters

In [27]:
gdf_h3_proj = gdf_h3.to_crs('EPSG:3857')

In [28]:
gdf_h3_proj[['num_schools', 'num_subways', 'bike_path_length', 'park_area']] = gdf_h3_proj.geometry.apply(
    lambda hex_geom: pd.Series(analyze_access(hex_geom))
)


In [29]:
gdf_h3_proj.head()

neighborhood boroughCode borough  \
892a1001067ffff     Allerton           2   Bronx   
892a100102bffff     Allerton           2   Bronx   
892a1001313ffff     Allerton           2   Bronx   
892a1001397ffff     Allerton           2   Bronx   
892a1001023ffff     Allerton           2   Bronx   

                                                              X.id  \
892a1001067ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a100102bffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a1001313ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a1001397ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a1001023ffff  http://nyc.pediacities.com/Resource/Neighborho...   

                                                          geometry  \
892a1001067ffff  POLYGON ((-8222481.225 4992990.858, -8222716.2...   
892a100102bffff  POLYGON ((-8222004.039 4993007.193, -8222239.0...   
892a1001313ffff  POLYGON ((-8223164.533 4991798.387, -8223399.4...   
892a1001397ffff  POLYGON ((-8221982.525 4992228.542, -8222217.5...   
892a1001023ffff  POLYGON ((-8221526.852 4993023.504, -8221761.8...   

                 num_schools  num_subways  bike_path_length     park_area  \
892a1001067ffff         26.0         13.0      33296.033540  5.656789e+06   
892a100102bffff         21.0         14.0      34306.053759  4.264377e+04   
892a1001313ffff         18.0         12.0      23960.576290  5.089437e+06   
892a1001397ffff         18.0         11.0      29583.351640  4.875261e+05   
892a1001023ffff         23.0          6.0      32950.084942  3.018169e+04   

                 index_score  
892a1001067ffff     0.137616  
892a100102bffff     0.137616  
892a1001313ffff     0.137616  
892a1001397ffff     0.137616  
892a1001023ffff     0.137616

In [30]:
gdf_h3_proj['h3_index'] = gdf_h3_proj.index

# Run the normalization analysis

In [31]:
import h3

In [33]:
# Normalize results
scaler = MinMaxScaler()
normalized_columns = ['num_schools', 'num_subways', 'bike_path_length', 'park_area']
gdf_h3_proj[normalized_columns] = scaler.fit_transform(gdf_h3_proj[normalized_columns])

# Aggregate results using neighboring cells
def aggregate_neighbors(h3_index):
    neighbors = h3.grid_ring(h3_index, 2)  # 2-ring
    neighbor_values = gdf_h3_proj[gdf_h3_proj['h3_index'].isin(neighbors)][normalized_columns].mean()
    return neighbor_values

gdf_h3_proj[normalized_columns] = gdf_h3_proj['h3_index'].apply(
    lambda h3_index: aggregate_neighbors(h3_index)
)

# # Final normalized analysis
gdf_h3_proj[normalized_columns] = scaler.fit_transform(gdf_h3_proj[normalized_columns])

# Save or visualize the results
gdf_h3_proj.to_file("access_index.geojson", driver="GeoJSON")

In [34]:
gdf_h3_proj.head(3)

neighborhood boroughCode borough  \
892a1001067ffff     Allerton           2   Bronx   
892a100102bffff     Allerton           2   Bronx   
892a1001313ffff     Allerton           2   Bronx   

                                                              X.id  \
892a1001067ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a100102bffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a1001313ffff  http://nyc.pediacities.com/Resource/Neighborho...   

                                                          geometry  \
892a1001067ffff  POLYGON ((-8222481.225 4992990.858, -8222716.2...   
892a100102bffff  POLYGON ((-8222004.039 4993007.193, -8222239.0...   
892a1001313ffff  POLYGON ((-8223164.533 4991798.387, -8223399.4...   

                 num_schools  num_subways  bike_path_length  park_area  \
892a1001067ffff     0.256694     0.060107          0.312545   0.163847   
892a100102bffff     0.245614     0.051647          0.316352   0.119683   
892a1001313ffff     0.283472     0.061443          0.230589   0.253628   

                 index_score         h3_index  
892a1001067ffff     0.137616  892a1001067ffff  
892a100102bffff     0.137616  892a100102bffff  
892a1001313ffff     0.137616  892a1001313ffff

# Create the total score

In [35]:
gdf_h3_proj['index_score'] = gdf_h3_proj['num_schools'] + gdf_h3_proj['num_subways'] + gdf_h3_proj['bike_path_length'] + gdf_h3_proj['park_area'] 

In [36]:
import leafmap

In [37]:
gdf_h3_map = gdf_h3_proj.to_crs('EPSG:4326')

In [38]:
m = leafmap.Map()
m.add_data(
    gdf_h3_map, column="index_score", scheme="Quantiles", cmap="Blues", legend_title="Index"
)
m

Map(center=[20, 0], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_out_text…